To run this, press "*Runtime*" and press "*Run all*" on a **free** Tesla T4 Google Colab instance!

<div class="align-center">
<a href="https://unsloth.ai/"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
<a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord%20button.png" width="145"></a>
<a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a></a> Join Discord if you need help + ⭐ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐
</div>

This notebook fine-tunes a powerful reasoning model on the **ARC Prize 2024 Dataset**. You will learn how to do [data prep for ARC](#Data), how to [train with GRPO](#Train), how to [run inference on ARC tasks](#Inference), & [how to save your model](#Save).

### News

Unsloth now supports Text-to-Speech (TTS) models. Read our [guide here](https://docs.unsloth.ai/basics/text-to-speech-tts-fine-tuning).

Read our **[Qwen3 Guide](https://docs.unsloth.ai/basics/qwen3-how-to-run-and-fine-tune)** and check out our new **[Dynamic 2.0](https://docs.unsloth.ai/basics/unsloth-dynamic-2.0-ggufs)** quants which outperforms other quantization methods!

Visit our docs for all our [model uploads](https://docs.unsloth.ai/get-started/all-our-models) and [notebooks](https://docs.unsloth.ai/get-started/unsloth-notebooks).

### Installation

In [1]:
%%capture
import os
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth vllm
else:
    # [NOTE] Do the below ONLY in Colab! Use [[pip install unsloth vllm]]
    !pip install --no-deps unsloth vllm==0.8.5.post1

In [2]:
#@title Colab Extra Install { display-mode: "form" }
%%capture
import os
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth vllm
else:
    !pip install --no-deps unsloth vllm==0.8.5.post1
    # [NOTE] Do the below ONLY in Colab! Use [[pip install unsloth vllm]]
    # Skip restarting message in Colab
    import sys, re, requests; modules = list(sys.modules.keys())
    for x in modules: sys.modules.pop(x) if "PIL" in x or "google" in x else None
    !pip install --no-deps bitsandbytes accelerate xformers==0.0.29.post3 peft "trl==0.15.2" triton cut_cross_entropy unsloth_zoo
    !pip install sentencepiece protobuf "datasets>=3.4.1" huggingface_hub hf_transfer
    !pip install transformers==4.51.3

    # vLLM requirements - vLLM breaks Colab due to reinstalling numpy
    f = requests.get("https://raw.githubusercontent.com/vllm-project/vllm/refs/heads/main/requirements/common.txt").content
    with open("vllm_requirements.txt", "wb") as file:
        file.write(re.sub(rb"(transformers|numpy|xformers)[^\n]{1,}\n", b"", f))
    !pip install -r vllm_requirements.txt

### Unsloth

**Goal:** To fine-tune `DeepSeek-R1-0528-Qwen3-8B` into an ARC (Abstraction and Reasoning Corpus) solver using the GRPO algorithm. We will use the official ARC Prize 2024 dataset and structure the code to be ready for the 2025 dataset.

Our reward function will be based on whether the model produces the correct JSON output grid for a given test task.

In [3]:
!pip install langid -qq

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 33.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done


In [4]:
from unsloth import FastLanguageModel
import torch

# ARC tasks can have complex descriptions and multiple examples.
# A larger sequence length is necessary.
# 4096 is a good starting point for a T4 GPU with 4-bit quantization.
max_seq_length = 4096
lora_rank = 32 # Larger rank = smarter, but slower

# The model name for fine-tuning
model_name = "unsloth/DeepSeek-R1-0528-Qwen3-8B"

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = model_name,
    max_seq_length = max_seq_length,
    load_in_4bit = True,
    fast_inference = True, # Enable vLLM fast inference
    max_lora_rank = lora_rank,
    gpu_memory_utilization = 0.8, # Adjust if out of memory
)

model = FastLanguageModel.get_peft_model(
    model,
    r = lora_rank, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = [
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj",
    ],
    lora_alpha = lora_rank*2, # *2 speeds up training
    use_gradient_checkpointing = "unsloth", # Reduces memory usage
    random_state = 3407,
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!
INFO 06-07 13:26:51 [importing.py:53] Triton module has been replaced with a placeholder.
INFO 06-07 13:26:51 [__init__.py:239] Automatically detected platform cuda.


Unrecognized keys in `rope_scaling` for 'rope_type'='yarn': {'attn_factor'}


==((====))==  Unsloth 2025.6.1: Fast Qwen3 patching. Transformers: 4.51.3. vLLM: 0.8.5.post1.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 7.5. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Unrecognized keys in `rope_scaling` for 'rope_type'='yarn': {'attn_factor'}


Unsloth: vLLM loading unsloth/deepseek-r1-0528-qwen3-8b-unsloth-bnb-4bit with actual GPU utilization = 79.24%
Unsloth: Your GPU has CUDA compute capability 7.5 with VRAM = 14.74 GB.
Unsloth: Using conservativeness = 1.0. Chunked prefill tokens = 4096. Num Sequences = 192.
Unsloth: vLLM's KV Cache can use up to 5.16 GB. Also swap space = 0 GB.


...

tokenizer_config.json:   0%|          | 0.00/11.3k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/11.4M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/472 [00:00<?, ?B/s]

chat_template.jinja:   0%|          | 0.00/5.15k [00:00<?, ?B/s]

Unsloth 2025.6.1 patched 36 layers with 36 QKV layers, 36 O layers and 36 MLP layers.


### <a name="Data"></a>Data Prep for ARC

For the ARC Prize task, we need to create a structured prompt that presents the problem clearly to the model. An effective prompt will include:
1.  **A system-level instruction** explaining the ARC task.
2.  **The training pairs** (input and output grids) to show the pattern.
3.  **The test input grid** for which the model must find the solution.
4.  A clear instruction for the model to provide **reasoning** and the **final JSON output**.

We will format the input grids and JSON data into a human-readable string for the model to process.

Let's see how our chat template behaves on an example:

In [6]:
import json

# Define the system prompt for ARC tasks
arc_system_prompt = """You are an expert in solving Abstraction and Reasoning Corpus (ARC) problems.
You will be given a task consisting of several training examples and a final test example.
Each example is a pair of input and output grids.
Your goal is to identify the underlying abstract pattern in the training examples and apply it to the test input grid to generate the correct output grid.

Analyze the provided pairs, describe your reasoning process step-by-step.
After your reasoning, provide the solution for the test case in a single JSON block.
The JSON output should be a single list of lists representing the output grid.
Example format:
<reasoning>
Here, I will explain my thought process for solving the task...
</reasoning>
```json
[[0, 1, 0], [1, 0, 1]] """

In [7]:
print(tokenizer.apply_chat_template([
    {"role" : "user", "content" : "What is 1+1?"},
    {"role" : "assistant", "content" : f"<think>I think it's 2.2</think>2"},
    {"role" : "user", "content" : "What is 1+1?"},
    {"role" : "assistant", "content" : f"<think>I think it's 2.2</think>2"},
], tokenize = False, add_generation_prompt = True))

<｜begin▁of▁sentence｜><｜User｜>What is 1+1?<｜Assistant｜>2<｜end▁of▁sentence｜><｜User｜>What is 1+1?<｜Assistant｜>2<｜end▁of▁sentence｜><｜Assistant｜>


### <a name="Data"></a>Data Prep for ARC


In [9]:

from datasets import load_dataset, concatenate_datasets

# Load ARC Prize 2024 training data
# Note: The ARC Prize 2025 dataset is not yet released.
# When it is, you can load it and concatenate it with the 2024 data.
# For example:
# dataset_2025 = load_dataset("arc-prize-2025/public-training", split="train")
# combined_dataset = concatenate_datasets([dataset_2024, dataset_2025])

dataset_2024 = load_dataset("arcprize/arc_agi_v1_public_eval", split="train")

# For demonstration, we'll just use the 2024 data
dataset = dataset_2024

print("ARC Dataset loaded:")
print(dataset)
print("\nExample from the dataset:")
print(dataset[0])

README.md:   0%|          | 0.00/168 [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/2000 [00:00<?, ?it/s]

00576224.json:   0%|          | 0.00/21.8k [00:00<?, ?B/s]

0a2355a6.json:   0%|          | 0.00/126k [00:00<?, ?B/s]

09c534e7.json:   0%|          | 0.00/182k [00:00<?, ?B/s]

...

a59b95c0.json:   0%|          | 0.00/12.7k [00:00<?, ?B/s]

HTTP Error 429 thrown while requesting HEAD https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/aa300dc3.json


a406ac07.json:   0%|          | 0.00/15.2k [00:00<?, ?B/s]

HTTP Error 429 thrown while requesting GET https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/aa18de87.json
HTTP Error 429 thrown while requesting HEAD https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/ac0c5833.json
HTTP Error 429 thrown while requesting HEAD https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/aab50785.json
Retrying in 1s [Retry 1/5].
HTTP Error 429 thrown while requesting HEAD https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/aa4ec2a5.json
Retrying in 1s [Retry 1/5].
HTTP Error 429 thrown while requesting HEAD https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/ac2e8ecf.

HTTPError: 429 Client Error: Too Many Requests for url: https://huggingface.co/datasets/arcprize/arc_agi_v1_public_eval/resolve/cf608c9c482ec5cbb555d6c7308ccb7edc27ff30/gpt-4-1-2025-04-14/a680ac02.json

Let's look at the first row:

In [ ]:
import json

def format_arc_prompt(example):
    """Formats an ARC task into a prompt for the model."""
    train_pairs = json.loads(example['train_pairs'])
    test_pairs = json.loads(example['test_pairs'])

    prompt = "### ARC Task\n"
    prompt += "Here are the training examples:\n"
    for i, pair in enumerate(train_pairs):
        prompt += f"--- Training Example {i+1} ---\n"
        prompt += f"Input:\n{json.dumps(pair['input'])}\n"
        prompt += f"Output:\n{json.dumps(pair['output'])}\n"

    prompt += "\nHere is the test input:\n"
    prompt += f"--- Test Example ---\n"
    prompt += f"Input:\n{json.dumps(test_pairs[0]['input'])}\n"
    prompt += "--- End of task ---\n"
    prompt += "Please provide your reasoning and the final JSON output for the test example."

    return prompt

def format_arc_solution(example):
    """Formats the ground truth solution."""
    test_pairs = json.loads(example['test_pairs'])
    # The "chosen" answer for GRPO is the correct JSON output.
    # We don't have pre-made reasoning, so the reward will focus on getting the JSON right.
    return json.dumps(test_pairs[0]['output'])

# Map the formatting functions to the dataset
dataset = dataset.map(lambda x: {
    "prompt" : [
        {"role": "system", "content": arc_system_prompt},
        {"role": "user", "content": format_arc_prompt(x)},
    ],
    "answer": format_arc_solution(x),
})

# Let's see the first processed row
print("Formatted Prompt for the first task:")
print(dataset[0]["prompt"][1]["content"])
print("\nExpected Answer (JSON):")
print(dataset[0]["answer"])

In [ ]:
import re
import json

# Regex to find the JSON block in the model's output
# It looks for ```json ... ``` or a raw [[...]]
json_match_regex = re.compile(r"```json\s*([\s\S]*?)\s*```|(\[\[[\s\S]*?\]\])", re.DOTALL)

def check_arc_solution(prompts, completions, answer, **kwargs):
    """
    Reward function for ARC tasks.
    It checks if the generated JSON matches the ground truth solution.
    """
    scores = []

    for completion_item, true_answer_json in zip(completions, answer):
        try:
            completion_text = completion_item[0]["content"]

            # Find the JSON part in the completion text
            match = json_match_regex.search(completion_text)
            if not match:
                scores.append(-2.0) # Penalty for not producing a JSON block
                continue

            # Extract the JSON string (it's in one of the groups)
            json_str = match.group(1) or match.group(2)
            if not json_str:
                scores.append(-2.0)
                continue

            # Parse the generated JSON and the ground truth JSON
            predicted_grid = json.loads(json_str)
            true_grid = json.loads(true_answer_json)

            # Compare the grids
            if predicted_grid == true_grid:
                scores.append(10.0)  # High reward for a perfect match
            else:
                scores.append(-1.0) # Penalty for correct format but wrong answer
        except (json.JSONDecodeError, TypeError, IndexError):
            scores.append(-5.0) # Heavy penalty for invalid format or errors

    return scores

In [ ]:
# Calculate prompt lengths and filter out excessively long ones
tokenized = dataset.map(
    lambda x: {"tokens" : tokenizer.apply_chat_template(x["prompt"], add_generation_prompt = True, tokenize = True)},
    batched = False, # Process one by one
)
tokenized = tokenized.map(lambda x: {"L" : len(x["tokens"])})

import numpy as np
# We keep 98% of the data to avoid OOM on very long prompts
maximum_length = int(np.quantile(tokenized["L"], 0.98))
print(f"Max prompt length will be set to: {maximum_length}")

# Filter the dataset
dataset = dataset.select(np.where(np.array(tokenized["L"]) <= maximum_length)[0])
del tokenized
print(f"Dataset filtered to {len(dataset)} samples.")

Let's map the dataset! and see the first row:

In [ ]:
max_prompt_length = maximum_length + 1 # Add a small buffer
# Completion length should be enough for reasoning and the JSON grid
max_completion_length = max_seq_length - max_prompt_length

from vllm import SamplingParams
vllm_sampling_params = SamplingParams(
    min_p = 0.1,
    top_p = 1.0,
    top_k = -1,
    seed = 3407,
    stop = [tokenizer.eos_token],
    include_stop_str_in_output = True,
)

from trl import GRPOConfig, GRPOTrainer
training_args = GRPOConfig(
    vllm_sampling_params = vllm_sampling_params,
    temperature = 1.0,
    learning_rate = 5e-6,
    weight_decay = 0.01,
    warmup_ratio = 0.1,
    lr_scheduler_type = "linear",
    optim = "adamw_8bit",
    logging_steps = 5,
    per_device_train_batch_size = 1,
    gradient_accumulation_steps = 4, # Increase for smoother training
    num_generations = 4, # Decrease if out of memory
    max_prompt_length = max_prompt_length,
    max_completion_length = max_completion_length,
    # num_train_epochs = 1, # Set to 1 for a full training run
    max_steps = 200, # Increase for a more thorough training
    save_steps = 50,
    report_to = "none", # Can use "wandb"
    output_dir = "outputs_arc",
)

We create a regex format to match the reasoning sections and answers:

In [ ]:
import re

# Add optional EOS token matching
solution_end_regex = rf"{reasoning_end}(.*)"

match_format = re.compile(solution_end_regex, re.DOTALL)
match_format

We verify it works:

In [ ]:
match_format.findall(
    "Let me think!</think>"\
    f"Hence, the solution is 2.",
)

In [ ]:
match_format.findall(
    "<think>Let me think!</think>"\
    f"\n\nHence, the solution is 2",
)

We now want to create a reward function to match the format exactly - we reward it with 3 points if it succeeds:

In [ ]:
def match_format_exactly(completions, **kwargs):
    scores = []
    for completion in completions:
        score = 0
        response = completion[0]["content"]
        # Match if format is seen exactly!
        if match_format.search(response) is not None: score += 3.0
        scores.append(score)
    return scores

If it fails, we want to reward the model if it at least follows the format partially, by counting each symbol:

In [ ]:
def match_format_approximately(completions, **kwargs):
    scores = []
    for completion in completions:
        score = 0
        response = completion[0]["content"]
        # Count how many keywords are seen - we penalize if too many!
        # If we see 1, then plus some points!

        # No need to reward <think> since we always prepend it!
        score += 0.5 if response.count(reasoning_start) == 1 else -1.0
        score += 0.5 if response.count(reasoning_end)   == 1 else -1.0
        scores.append(score)
    return scores

We want to extract the generated answer, and reward or penalize it! We also reward it based on how close the answer is to the true one via ratios:

In [ ]:
def check_answer(prompts, completions, answer, **kwargs):
    question = prompts[0][-1]["content"]
    responses = [completion[0]["content"] for completion in completions]

    extracted_responses = [
        guess.group(1)
        if (guess := match_format.search(r)) is not None else None \
        for r in responses
    ]

    scores = []
    for guess, true_answer in zip(extracted_responses, answer):
        score = 0
        if guess is None:
            scores.append(-2.0)
            continue
        # Correct answer gets 5 points!
        if guess == true_answer:
            score += 5.0
        # Match if spaces are seen, but less reward
        elif guess.strip() == true_answer.strip():
            score += 3.5
        else:
            # We also reward it if the answer is close via ratios!
            # Ie if the answer is within some range, reward it!
            try:
                ratio = float(guess) / float(true_answer)
                if   ratio >= 0.9 and ratio <= 1.1: score += 2.0
                elif ratio >= 0.8 and ratio <= 1.2: score += 1.5
                else: score -= 2.5 # Penalize wrong answers
            except:
                score -= 4.5 # Penalize
        scores.append(score)
    return scores

Also sometimes it might not be 1 number as the answer, but like a sentence for example "The solution is $20" -> we extract 20.

We also remove possible commas for example as in 123,456

In [ ]:
match_numbers = re.compile(
    r".*?[\s]{0,}([-]?[\d\.\,]{1,})",
    flags = re.MULTILINE | re.DOTALL
)
print(match_numbers.findall("  0.34  "))
print(match_numbers.findall("  123,456  "))
print(match_numbers.findall("  -0.234  "))
print(match_numbers.findall("17"))

Finally, we will try to enforce the thinking process to be in Bahasa Indonesia. This is a simple version of the `language consistency reward` that is used in DeepSeek R1 paper

In [ ]:
import langid

def get_lang(text: str) -> str:
    if not text:
        return "und"
    lang, _ = langid.classify(text)
    return lang


print(get_lang("Hello, How are you")) # This should return en
print(get_lang("Aku berpikir kalau aku adalah kamu")) # This should return id
print(get_lang("我在这里")) # This should return zh

In [ ]:
import re

def format_and_language_reward_func(completions, **kwargs):
    scores = []

    for completion_item in completions:
        if not completion_item or not isinstance(completion_item[0], dict) or "content" not in completion_item[0]:
            scores.append(-5.0)
            print(f"Warning: Malformed completion item, assigning default low score: {completion_item}")
            continue

        content = completion_item[0]["content"]

        lang = get_lang(content)

        if lang == 'id':
            score = 5.0
        elif lang == 'en':
            score = -3.0
        elif lang == 'zh':
            score = -3.0
        else:
            score = -5.0

        scores.append(score)

    return scores

In [ ]:
prompts = [
    [{"role": "assistant", "content": "What is the result of (1 + 2) * 4?"}],
    [{"role": "assistant", "content": "What is the result of (3 + 1) * 2?"}],
]
completions = [
    [{"role": "assistant", "content": "<think>The sum of 1 and 2 is 3, which we multiply by 4 to get 12.</think><answer>(1 + 2) * 4 = 12</answer>"}],
    [{"role": "assistant", "content": "The sum of 3 and 1 is 4, which we multiply by 2 to get 8. So (3 + 1) * 2 = 8."}],
]
format_and_language_reward_func(prompts=prompts, completions=completions)

We now prepare our main function which will print out the generated responses and the true answer, along with another reward function which converts text to float via `float` and sees if it's the same.

In [ ]:
global PRINTED_TIMES
PRINTED_TIMES = 0
global PRINT_EVERY_STEPS
PRINT_EVERY_STEPS = 5

def check_numbers(prompts, completions, answer, **kwargs):
    question = prompts[0][-1]["content"]
    responses = [completion[0]["content"] for completion in completions]

    extracted_responses = [
        guess.group(1)
        if (guess := match_numbers.search(r)) is not None else None \
        for r in responses
    ]

    scores = []
    # Print only every few steps
    global PRINTED_TIMES
    global PRINT_EVERY_STEPS
    if PRINTED_TIMES % PRINT_EVERY_STEPS == 0:
        print(
            '*'*20 + f"Question:\n{question}", f"\nAnswer:\n{answer[0]}", f"\nResponse:\n{responses[0]}", f"\nExtracted:\n{extracted_responses[0]}"
        )
    PRINTED_TIMES += 1

    for guess, true_answer in zip(extracted_responses, answer):
        if guess is None:
            scores.append(-2.5)
            continue
        # Convert to numbers
        try:
            true_answer = float(true_answer.strip())
            # Remove commas like in 123,456
            guess       = float(guess.strip().replace(",", ""))
            scores.append(3.5 if guess == true_answer else -1.5)
        except:
            scores.append(0)
            continue
    return scores

Get the top 90% prompt length so we don't accidentally truncate them!

Ie we'll remove the top 10% long prompts.

In [ ]:
tokenized = dataset.map(
    lambda x: {"tokens" : tokenizer.apply_chat_template(x["prompt"], add_generation_prompt = True, tokenize = True)},
    batched = True,
)
print(tokenizer.decode(tokenized[0]["tokens"]))
tokenized = tokenized.map(lambda x: {"L" : len(x["tokens"])})

import numpy as np
maximum_length = int(np.quantile(tokenized["L"], 0.9))
print("Max Length = ", maximum_length)

# Filter only samples smaller than 90% max length
dataset = dataset.select(np.where(np.array(tokenized["L"]) <= maximum_length)[0])
del tokenized

<a name="Train"></a>
### Train the model

Now we set up the `GRPOTrainer` with our custom ARC reward function and start training. The goal is to see the `reward/check_arc_solution` column increase over time. It may take many steps before the model starts generating valid JSON and getting positive rewards.

In [ ]:
global PRINTED_TIMES
PRINTED_TIMES = 0
global PRINT_EVERY_STEPS
PRINT_EVERY_STEPS = 20 # Print a sample every 20 steps

def print_one_completion(prompts, completions, answer, **kwargs):
    """A dummy reward function just to print a sample during training."""
    global PRINTED_TIMES, PRINT_EVERY_STEPS
    if PRINTED_TIMES % PRINT_EVERY_STEPS == 0:
        print("="*20 + f" Step Sample " + "="*20)
        print("USER PROMPT:\n" + prompts[0][-1]['content'])
        print("\nMODEL COMPLETION:\n" + completions[0][0]['content'])
        print("\nGROUND TRUTH:\n" + answer[0])
        print("="*53)
    PRINTED_TIMES += 1
    return [0.0] * len(completions) # Return a neutral score

trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    reward_funcs = [
        check_arc_solution,
        print_one_completion,
    ],
    args = training_args,
    train_dataset = dataset,
)
trainer.train()

And let's run the trainer! If you scroll up, you'll see a table of rewards. The goal is to see the `reward` column increase!

You might have to wait 150 to 200 steps for any action. You'll probably get 0 reward for the first 100 steps. Please be patient!

| Step | Training Loss | reward    | reward_std | completion_length | kl       |
|------|---------------|-----------|------------|-------------------|----------|
| 1    | 0.000000      | 0.125000  | 0.000000   | 200.000000        | 0.000000 |
| 2    | 0.000000      | 0.072375  | 0.248112   | 200.000000        | 0.000000 |
| 3    | 0.000000      | -0.079000 | 0.163776   | 182.500000        | 0.000005 |


<a name="Inference"></a>
### Inference

Let's test the fine-tuned model on a new ARC task from the validation set. We'll load the LoRA adapters we just trained and see if the model can solve a problem it hasn't seen during training.

In [ ]:
# Save the trained LoRA adapters
model.save_lora("arc_lora_model")

And now with the LoRA we just trained with GRPO - we first save the LoRA first!

Verify LoRA is actually trained!

In [ ]:
# Load a sample from the validation set for testing
validation_dataset = load_dataset("arc-prize-2024/public-validation", split="train")
test_sample = validation_dataset[10] # Pick a sample

# Format the prompt for the test sample
messages = [
    {"role": "system", "content": arc_system_prompt},
    {"role": "user", "content": format_arc_prompt(test_sample)},
]

text_prompt = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt = True,
    tokenize = False,
)

# Set sampling parameters for inference
sampling_params = SamplingParams(
    temperature = 0.1, # Lower temperature for more deterministic output
    top_p = 0.9,
    max_tokens = 1024, # Allow enough tokens for reasoning and JSON
)

# Generate the output using the fine-tuned LoRA
output = model.fast_generate(
    text_prompt,
    sampling_params = sampling_params,
    lora_request = model.load_lora("arc_lora_model"),
)[0].outputs[0].text

Now we load the LoRA and test. We tested without using our custom system prompt which should not (or minimal) affect toward the model's original reasoning ability.:

In [ ]:
# Display the results and check for correctness
print("✅ MODEL GENERATION")
print("="*60)
print(output)
print("="*60)

# Check if the generated solution is correct
ground_truth_json = format_arc_solution(test_sample)
ground_truth_grid = json.loads(ground_truth_json)

match = json_match_regex.search(output)
if match:
    json_str = match.group(1) or match.group(2)
    try:
        predicted_grid = json.loads(json_str)
        if predicted_grid == ground_truth_grid:
            print("\n🎉 CORRECT! The generated grid matches the ground truth.")
        else:
            print("\n❌ INCORRECT. The grid does not match.")
            print("Expected:\n", json.dumps(ground_truth_grid))
            print("Got:\n", json.dumps(predicted_grid))
    except json.JSONDecodeError:
        print("\n❌ FAILED. The output contained invalid JSON.")
else:
    print("\n❌ FAILED. No JSON output block found in the generation.")

Next, let's test using our system prompt which should use the new language :

In [ ]:
messages = [
    {"role": "system", "content": system_prompt},
    {"role": "user",   "content": "Solve (x + 2)^2 = 0"},
]

text = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt = True, # Must add for generation
    tokenize = False,
)
from vllm import SamplingParams
sampling_params = SamplingParams(
    temperature = 1.0,
    top_k = 50,
    max_tokens = 2048,
)
output = model.fast_generate(
    text,
    sampling_params = sampling_params,
    lora_request = model.load_lora("grpo_lora"),
)[0].outputs[0].text

output

Lets compare our results with system prompt but without our LoRA

In [ ]:
messages = [
    {"role": "system", "content": system_prompt},
    {"role": "user",   "content": "Solve (x + 2)^2 = 0"},
]

text = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt = True, # Must add for generation
    tokenize = False,
)
from vllm import SamplingParams
sampling_params = SamplingParams(
    temperature = 1.0,
    top_k = 50,
    max_tokens = 2048,
)
output = model.fast_generate(
    text,
    sampling_params = sampling_params,
    lora_request = None,
)[0].outputs[0].text

output

Let's take 20 samples, and compare the the amount of using our LoRA and not using it, and see which one has better amount of correct language

In [ ]:
sample_dataset = dataset.shuffle(seed = 3407).select(range(20))
sample_dataset

Our reasoning model is much better - it's not always correct, since we only trained it for an hour or so - it'll be better if we extend the sequence length and train for longer!

<a name="Save"></a>
### Saving to float16 for VLLM

We also support saving to `float16` directly. Select `merged_16bit` for float16 or `merged_4bit` for int4. We also allow `lora` adapters as a fallback. Use `push_to_hub_merged` to upload to your Hugging Face account! You can go to https://huggingface.co/settings/tokens for your personal tokens.

In [ ]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False: model.save_pretrained_merged("model", tokenizer, save_method = "lora",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "lora", token = "")

### GGUF / llama.cpp Conversion
To save to `GGUF` / `llama.cpp`, we support it natively now! We clone `llama.cpp` and we default save it to `q8_0`. We allow all methods like `q4_k_m`. Use `save_pretrained_gguf` for local saving and `push_to_hub_gguf` for uploading to HF.

Some supported quant methods (full list on our [Wiki page](https://github.com/unslothai/unsloth/wiki#gguf-quantization-options)):
* `q8_0` - Fast conversion. High resource use, but generally acceptable.
* `q4_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q4_K.
* `q5_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q5_K.

[**NEW**] To finetune and auto export to Ollama, try our [Ollama notebook](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3_(8B)-Ollama.ipynb)

In [ ]:
# Save to 8bit Q8_0
if False: model.save_pretrained_gguf("model", tokenizer,)
# Remember to go to https://huggingface.co/settings/tokens for a token!
# And change hf to your username!
if False: model.push_to_hub_gguf("hf/model", tokenizer, token = "")

# Save to 16bit GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "f16")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "f16", token = "")

# Save to q4_k_m GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "q4_k_m")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "q4_k_m", token = "")

# Save to multiple GGUF options - much faster if you want multiple!
if False:
    model.push_to_hub_gguf(
        "hf/model", # Change hf to your username!
        tokenizer,
        quantization_method = ["q4_k_m", "q8_0", "q5_k_m",],
        token = "",
    )

Now, use the `model-unsloth.gguf` file or `model-unsloth-Q4_K_M.gguf` file in llama.cpp or a UI based system like Jan or Open WebUI. You can install Jan [here](https://github.com/janhq/jan) and Open WebUI [here](https://github.com/open-webui/open-webui)

And we're done! If you have any questions on Unsloth, we have a [Discord](https://discord.gg/unsloth) channel! If you find any bugs or want to keep updated with the latest LLM stuff, or need help, join projects etc, feel free to join our Discord!

Some other links:
1. Train your own reasoning model - Llama GRPO notebook [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.1_(8B)-GRPO.ipynb)
2. Saving finetunes to Ollama. [Free notebook](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3_(8B)-Ollama.ipynb)
3. Llama 3.2 Vision finetuning - Radiography use case. [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.2_(11B)-Vision.ipynb)
6. See notebooks for DPO, ORPO, Continued pretraining, conversational finetuning and more on our [documentation](https://docs.unsloth.ai/get-started/unsloth-notebooks)!

<div class="align-center">
  <a href="https://unsloth.ai"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
  <a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord.png" width="145"></a>
  <a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a>

  Join Discord if you need help + ⭐️ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐️
</div>
